In [ ]:
%load_ext autoreload
%autoreload 2

In [ ]:
!pip install optuna optuna-dashboard
!pip install git+https://github.com/R-N/ml-utility-loss
!pip install git+https://github.com/R-N/ml-utility-loss --force-reinstall --no-deps

  Cloning https://github.com/R-N/ml-utility-loss to /tmp/pip-req-build-fqzb6w1k
  Running command git clone --filter=blob:none --quiet https://github.com/R-N/ml-utility-loss /tmp/pip-req-build-fqzb6w1k
  Resolved https://github.com/R-N/ml-utility-loss to commit e9512918d69ed70bcd15f1c49c3e237aef190374
  Preparing metadata (setup.py) ... done
  Cloning https://github.com/R-N/ml-utility-loss to /tmp/pip-req-build-vpxbfeox
  Running command git clone --filter=blob:none --quiet https://github.com/R-N/ml-utility-loss /tmp/pip-req-build-vpxbfeox
  Resolved https://github.com/R-N/ml-utility-loss to commit e9512918d69ed70bcd15f1c49c3e237aef190374
  Preparing metadata (setup.py) ... done
  Created wheel for ml-utility-loss: filename=ml_utility_loss-0.1.1-py3-none-any.whl size=378135 sha256=b56375e2780574b57742479287c4d9caaddaa28e9087d2856957506a6c4a529b
  Stored in directory: /tmp/pip-ephem-wheel-cache-clfcxhqn/wheels/54/30/38/31c28079b5f07b6c793211d38f72e7f0be6764bfdfe016df74
Successfully buil

In [ ]:
%cd /content
!curl -Ls https://github.com/ekzhang/bore/releases/download/v0.4.0/bore-v0.4.0-x86_64-unknown-linux-musl.tar.gz | tar zx -C /usr/bin
!curl -Lo /usr/bin/cloudflared https://github.com/cloudflare/cloudflared/releases/latest/download/cloudflared-linux-amd64 && chmod +x /usr/bin/cloudflared

/content
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
100 34.7M  100 34.7M    0     0  22.8M      0  0:00:01  0:00:01 --:--:-- 33.8M


In [ ]:
%cd /content
!rm -rf ml-utility-loss
!git clone https://github.com/R-N/ml-utility-loss
%cd ml-utility-loss
!rm -rf ml_utility_loss

/content
Cloning into 'ml-utility-loss'...
remote: Enumerating objects: 54455, done.
remote: Counting objects: 100% (7368/7368), done.
remote: Compressing objects: 100% (3271/3271), done.
remote: Total 54455 (delta 4163), reused 7285 (delta 4081), pack-reused 47087
Receiving objects: 100% (54455/54455), 239.42 MiB | 12.87 MiB/s, done.
Resolving deltas: 100% (6211/6211), done.
Updating files: 100% (50325/50325), done.
/content/ml-utility-loss


In [ ]:
datasets = [
    "insurance",
    "treatment",
    "contraceptive"
]

model_dir = "/content/drive/MyDrive/rizqinur2010/Documents/ITS/Tesis/Model/"

In [87]:
import pandas as pd
import numpy as np
import json
import os

dataset_dir = "datasets"
dataset_name = "insurance"

df = pd.read_csv(os.path.join(dataset_dir, f"{dataset_name}.csv"))
with open(os.path.join(dataset_dir, f"{dataset_name}.json")) as f:
    info = json.load(f)

In [88]:
from ml_utility_loss.util import split_df_ratio

task = info["task"]
target = info["target"]
cat_features = info["cat_features"]
mixed_features = info["mixed_features"]
longtail_features = info["longtail_features"]
integer_features = info["integer_features"]

dfs = {
    "df": df,
}
dfs_test = {}
for i in range(5):
    train, test = split_df_ratio(df, ratio=0.2, i=i, seed=42)
    dfs[i] = train
    dfs_test[i] = test


In [89]:
from ml_utility_loss.util import mkdir

model_name = "tab_ddpm"
df_name = 4
#model_name_2 = f"{model_name}_{dataset_name}_{df_name}"
model_dir_2 = os.path.join(model_dir, model_name, dataset_name, str(df_name))
mkdir(model_dir_2)
model_path = os.path.join(model_dir_2, f"model.pt")
diffusion_path = os.path.join(model_dir_2, f"diffusion.pt")
trainer_path = os.path.join(model_dir_2, f"trainer.pt")
model_state_path = os.path.join(model_dir_2, f"model_state.json")
diffusion_state_path = os.path.join(model_dir_2, f"diffusion_state.json")
params_path = os.path.join(model_dir_2, f"params.json")

In [90]:
print(model_path)

/content/drive/MyDrive/rizqinur2010/Documents/ITS/Tesis/Model/tab_ddpm/insurance/4/model.pt


In [91]:

from ml_utility_loss.tuning import create_objective
from ml_utility_loss.synthesizers.tab_ddpm.params.default import RTDL_PARAMS
import ml_utility_loss.synthesizers.tab_ddpm.params as PARAMS
from ml_utility_loss.util import filter_dict_2, filter_dict
from copy import deepcopy

params = getattr(PARAMS, dataset_name).BEST

model_params={
    **params,
}

n_layers = model_params.pop("n_layers")
d_layers_0 = model_params.pop("d_layers_0")
d_layers_i = model_params.pop("d_layers_i")
d_layers_n = model_params.pop("d_layers_n")
d_layers = [
    d_layers_0,
    *[d_layers_i for _ in range(n_layers-2)],
    d_layers_n,
]
model_params["d_layers"] = d_layers

rtdl_params = filter_dict(model_params, RTDL_PARAMS)
model_params = {k: v for k, v in model_params.items() if k not in rtdl_params}
model_params["rtdl_params"] = rtdl_params
model_params_ = deepcopy(model_params)

In [92]:
from ml_utility_loss.synthesizers.tvae.wrapper import TVAE
from ml_utility_loss.synthesizers.tab_ddpm.pipeline import train as _train, sample as _sample

train = dfs[df_name]

model, diffusion, trainer = _train(
    train,
    task_type=task,
    target=target,
    cat_features=cat_features,
    **model_params,
)
# Create synthetic data
synth_df = _sample(
    diffusion,
    batch_size=model_params["batch_size"],
    num_samples=len(train)
)

/usr/local/lib/python3.10/dist-packages/delu/_utils.py:16: DeLUDeprecationWarning: The function improve_reproducibility` is deprecated and will be removed in future releases. Instead, use `delu.random.seed` and manually set flags mentioned in the `PyTorch docs on reproducibility <https://pytorch.org/docs/stable/notes/randomness.html>`_
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_encoders.py:868: FutureWarning: `sparse` was renamed to `sparse_output` in version 1.2 and will be removed in 1.4. `sparse_output` is ignored unless you leave `sparse` to its default value.
  warnings.warn(


[0]
11
{'rtdl_params': {'dropout': 0.07319902815233517, 'd_layers': [512, 512, 512, 512, 512, 2048]}, 'is_y_cond': True, 'd_in': 11}
Step 10/42617 MLoss: 0.0 GLoss: 0.9943 Sum: 0.9943
Step 20/42617 MLoss: 0.0 GLoss: 0.9767 Sum: 0.9767
Step 30/42617 MLoss: 0.0 GLoss: 0.8696 Sum: 0.8696
Step 40/42617 MLoss: 0.0 GLoss: 0.736 Sum: 0.736
Step 50/42617 MLoss: 0.0 GLoss: 0.6526 Sum: 0.6526
Step 60/42617 MLoss: 0.0 GLoss: 0.6061 Sum: 0.6061
Step 70/42617 MLoss: 0.0 GLoss: 0.5551 Sum: 0.5551
Step 80/42617 MLoss: 0.0 GLoss: 0.5202 Sum: 0.5202
Step 90/42617 MLoss: 0.0 GLoss: 0.5132 Sum: 0.5132
Step 100/42617 MLoss: 0.0 GLoss: 0.4983 Sum: 0.4983
Step 110/42617 MLoss: 0.0 GLoss: 0.4982 Sum: 0.4982
Step 120/42617 MLoss: 0.0 GLoss: 0.4895 Sum: 0.4895
Step 130/42617 MLoss: 0.0 GLoss: 0.4801 Sum: 0.4801
Step 140/42617 MLoss: 0.0 GLoss: 0.4709 Sum: 0.4709
Step 150/42617 MLoss: 0.0 GLoss: 0.4726 Sum: 0.4726
Step 160/42617 MLoss: 0.0 GLoss: 0.4611 Sum: 0.4611
Step 170/42617 MLoss: 0.0 GLoss: 0.4667 Sum: 0

/usr/local/lib/python3.10/dist-packages/delu/_utils.py:16: DeLUDeprecationWarning: The function improve_reproducibility` is deprecated and will be removed in future releases. Instead, use `delu.random.seed` and manually set flags mentioned in the `PyTorch docs on reproducibility <https://pytorch.org/docs/stable/notes/randomness.html>`_
  warnings.warn(


Sample timestep    0


In [93]:
import types
isinstance(trainer, types.GeneratorType)

False

In [94]:
import torch
from copy import deepcopy
import json

torch.save(model, model_path)
torch.save(diffusion, diffusion_path)
#torch.save(trainer, trainer_path)
torch.save(deepcopy(model.state_dict()), model_state_path)
torch.save(deepcopy(diffusion.state_dict()), diffusion_state_path)
with open(params_path, "w") as f:
    json.dump(model_params_, f, indent=4)

In [95]:
synth_path = os.path.join(model_dir_2, f"synth.csv")
train_path = os.path.join(model_dir_2, f"train.csv")
val_path = os.path.join(model_dir_2, f"val.csv")
test_path = os.path.join(model_dir_2, f"test.csv")

synth_df.to_csv(synth_path)
dfs[df_name].to_csv(train_path)
dfs_test[df_name].to_csv(val_path)
dfs_test[df_name].to_csv(test_path)